In [1]:
import sys
sys.path.append("../") # go to parent dir

%load_ext autoreload
%autoreload 2

In [2]:
from evrp_gdg.utils.utilities import create_optimal_edges, create_json_out, update_instance_json, read_instance_json_str, convert_txt_instances_to_csv
from evrp_gdg.utils.plot import plot_interactive_graph, plot_evrptwv2g
from evrp_gdg.milp.evrptw_gdp import EVRPTW

import pandas as pd
import numpy as np

import json

pd.options.plotting.backend = "plotly"

# Problem type options

Objective options: {Schneider} OR {OpEx CapEx Cycle EA DCM Delivery}

Constraint options: {Start=End FullStart=End NoXkappaBounds NoMinVehicles NoSymmetry NoXd}

Transformation methods: {Hull} OR {BigM}

In [3]:
# instance = 'r104C5'
# instance = 'r105C5'
# instance = 'r201C10'
# instance = 'rc108C10'
# instance = 'c103C15'
# instance = 'c202C15'
# instance = 'rc103C15'
# instance = 'r105C15'
# instance = 'r202C15'
# instance = 'r102C15'

instance = 'c103C5_'
# instance = 'c101C10_'
# instance = 'c106C15_e'
# instance = 'r105C5_e'

fpath = 'config/test_instances/' + instance + '.csv'

In [18]:
m = EVRPTW(problem_type='GDP BigM OpEx CapEx Cycle EA DCM Delivery')
# m.full_solve(fpath)
m.import_instance(fpath)
m.make_instance()
m.make_solver()

2021-05-02 08:54:52 INFO     Building abstract model
2021-05-02 08:54:52 INFO     Defining parameters and sets
2021-05-02 08:54:52 INFO     Defining variables
2021-05-02 08:54:52 INFO     Defining disjuncts and disjunction
2021-05-02 08:54:52 INFO     Importing EVRPTW MILP instance: c103C5_
2021-05-02 08:54:52 INFO     Reading CSV
2021-05-02 08:54:52 INFO     Creating graph
2021-05-02 08:54:52 INFO     Creating timeseries data
2021-05-02 08:54:52 INFO     Creating duplicates and extended graph
2021-05-02 08:54:52 INFO     Using Scipy euclidian distances to generate distance matrix
2021-05-02 08:54:52 INFO     Calculating distance matrix
2021-05-02 08:54:52 INFO     Creating parameters
2021-05-02 08:54:52 INFO     Creating instance
2021-05-02 08:55:00 INFO     Problem type: GDP BigM OpEx CapEx Cycle EA DCM Delivery


In [19]:
for idx in m.instance.E:
    m.instance.ArcOnBool[idx].associate_binary_var(m.instance.ArcOn[idx].indicator_var)
    m.instance.ArcOffBool[idx].associate_binary_var(m.instance.ArcOff[idx].indicator_var)
    
for s in m.instance.S_:
    for j in m.instance.V1_:
        if s != j:
            for t in m.instance.T:
                m.instance.EVChargeDischargeBool[s,j,t].associate_binary_var(m.instance.EVChargeDischarge[s,j,t].indicator_var)
                m.instance.EVIdleBool[s,j,t].associate_binary_var(m.instance.EVIdle[s,j,t].indicator_var)

In [20]:
# from pyomo.environ import *
# from pyomo.gdp import *
# def ArcOnThen_(m, i, j, t):
#     '''EV visiting charging station i at time t may charge or discharge'''
#     if i != j:
#         return m.ArcOnBool[i,j].implies(xor(m.EVChargeDischargeBool[i,j,t], m.EVIdleBool[i,j,t]))
#     else:
#         return Constraint.Skip
# m.instance.ArcOnThen_ = LogicalConstraint(m.instance.S_, m.instance.V1_, m.instance.T, rule=ArcOnThen_)
# 
# def ArcOffThen_(m, i, j, t):
#     '''EV not visiting charging station i at time t stays idle'''
#     if i != j:
#         return m.ArcOffBool[i,j].implies(m.EVIdleBool[i,j,t])
#     else:
#         return Constraint.Skip
# m.instance.ArcOffThen_ = LogicalConstraint(m.instance.S_, m.instance.V1_, m.instance.T, rule=ArcOffThen_)

# Convert logical constraints to normal constraints

from pyomo.environ import *
from pyomo.gdp import *
def ArcOnThen_(m, i, j, t):
    '''EV visiting charging station i at time t may charge or discharge'''
    if i != j:
        return m.ArcOn[i,j].indicator_var - m.EVChargeDischarge[i,j,t].indicator_var + m.EVIdle[i,j,t].indicator_var >= 0
    else:
        return Constraint.Skip
m.instance.ArcOnThen_ = Constraint(m.instance.S_, m.instance.V1_, m.instance.T, rule=ArcOnThen_)

def ArcOffThen_(m, i, j, t):
    '''EV not visiting charging station i at time t stays idle'''
    if i != j:
        return m.ArcOff[i,j].indicator_var - m.EVIdle[i,j,t].indicator_var <= 0
    else:
        return Constraint.Skip
m.instance.ArcOffThen_ = Constraint(m.instance.S_, m.instance.V1_, m.instance.T, rule=ArcOffThen_)

In [21]:
# m.instance.ArcOffThen_.pprint()

In [22]:
problem_type = m.problem_type.lower().split() #TODO: make problem type list a class property to share with build_model
if 'hull' in problem_type:
    xfrm = TransformationFactory('gdp.hull')
elif 'bigm' in problem_type:
    xfrm = TransformationFactory('gdp.bigm')
xfrm.apply_to(m.instance)

In [23]:
# m.instance.pprint()

In [24]:
m.opt.solve(m.instance, tee=True, options=m.solve_options)

Using license file C:\gurobi910\win64\gurobi.lic
Academic license - for non-commercial use only - expires 2021-06-13
Read LP format model from file C:\Users\berwa\AppData\Local\Temp\tmpyqme9ngl.pyomo.lp
Reading time = 1.56 seconds
x18741: 67862 rows, 18741 columns, 1666037 nonzeros
Changed value of parameter TimeLimit to 3600.0
   Prev: inf  Min: 0.0  Max: inf  Default: inf
Gurobi Optimizer version 9.1.0 build v9.1.0rc0 (win64)
Thread count: 4 physical cores, 8 logical processors, using up to 8 threads
Optimize a model with 67862 rows, 18741 columns and 1666037 nonzeros
Model fingerprint: 0x5d675795
Model has 4326 quadratic constraints
Variable types: 4974 continuous, 13767 integer (13767 binary)
Coefficient statistics:
  Matrix range     [3e-01, 3e+03]
  QMatrix range    [1e+00, 1e+00]
  QLMatrix range   [4e+00, 1e+03]
  Objective range  [1e-02, 1e+03]
  Bounds range     [3e-01, 1e+03]
  RHS range        [3e-01, 2e+03]
Presolve removed 48991 rows and 10278 columns (presolve time = 5s)

{'Problem': [{'Name': 'x18741', 'Lower bound': 1077.8179585052014, 'Upper bound': 1077.8246416742516, 'Number of objectives': 1, 'Number of constraints': 72188, 'Number of variables': 18741, 'Number of binary variables': 13767, 'Number of integer variables': 13767, 'Number of continuous variables': 4974, 'Number of nonzeros': 1666037, 'Sense': 'minimize'}], 'Solver': [{'Status': 'ok', 'Return code': '0', 'Message': 'Model was solved to optimality (subject to tolerances), and an optimal solution is available.', 'Termination condition': 'optimal', 'Termination message': 'Model was solved to optimality (subject to tolerances), and an optimal solution is available.', 'Wall time': '243.36322212219238', 'Error rc': 0, 'Time': 245.59805583953857}], 'Solution': [OrderedDict([('number of solutions', 0), ('number of solutions displayed', 0)])]}

In [ ]:
# x, xp, traces, routes = plot_evrptwv2g(m, save=False)

In [ ]:
# m.instance.ArcOnBool.pprint()

In [26]:
from pyomo.core.plugins.transform.logical_to_linear import *
update_boolean_vars_from_binary(m.instance)

In [21]:
# update_boolean_vars_from_binary_custom(m.instance)

In [12]:
for idx in m.instance.ArcOnBool:
#     print(idx)
    if m.instance.ArcOnBool[idx].value is True:
        print(m.instance.ArcOnBool[idx])

ArcOnBool[D0,C65]
ArcOnBool[S0_0,C98]
ArcOnBool[S15_0,C57]
ArcOnBool[C20,C24]
ArcOnBool[C98,C20]
ArcOnBool[C65,S0_0]
ArcOnBool[C57,D1]
ArcOnBool[C24,S15_0]


In [41]:
m.instance.xw.pprint()

xw : Size=9, Index=V01_
    Key   : Lower : Value              : Upper : Fixed : Stale : Domain
      C20 :     0 :  663.2151120211004 :  1236 : False : False : NonNegativeReals
      C24 :     0 :  758.2151120211004 :  1236 : False : False : NonNegativeReals
      C57 :     0 : 1051.0453610171874 :  1236 : False : False : NonNegativeReals
      C65 :     0 :               67.0 :  1236 : False : False : NonNegativeReals
      C98 :     0 :  535.6784632628535 :  1236 : False : False : NonNegativeReals
       D0 :     0 :                0.0 :  1236 : False : False : NonNegativeReals
       D1 :     0 :             1236.0 :  1236 : False : False : NonNegativeReals
     S0_0 :     0 :  169.8062484748657 :  1236 : False : False : NonNegativeReals
    S15_0 :     0 :              876.0 :  1236 : False : False : NonNegativeReals


In [42]:
# m.instance.EVChargeDischargeBool.pprint()

In [43]:
# for idx in m.instance.EVChargeDischargeBool:
# #     print(idx)
#     if m.instance.EVChargeDischargeBool[idx].value is True:
# #         print(idx)
#         print(m.instance.EVChargeDischargeBool[idx])

# #     if m.instance.EVChargeDischargeBool[idx].value is True:
# #         print('Var: {} --> Value: {}'.format(m.instance.EVChargeDischargeBool[idx], m.instance.EVChargeDischargeBool[idx].value))

In [44]:
for idx in m.instance.EVIdleBool:
#     print(idx)
    if m.instance.EVIdleBool[idx].value is True:
        print(m.instance.EVIdleBool[idx])

EVIdleBool[S0_0,D1,0]
EVIdleBool[S0_0,D1,4]
EVIdleBool[S0_0,D1,8]
EVIdleBool[S0_0,D1,12]
EVIdleBool[S0_0,D1,16]
EVIdleBool[S0_0,D1,20]
EVIdleBool[S0_0,D1,24]
EVIdleBool[S0_0,D1,28]
EVIdleBool[S0_0,D1,32]
EVIdleBool[S0_0,D1,36]
EVIdleBool[S0_0,D1,40]
EVIdleBool[S0_0,D1,44]
EVIdleBool[S0_0,D1,48]
EVIdleBool[S0_0,D1,52]
EVIdleBool[S0_0,D1,56]
EVIdleBool[S0_0,D1,60]
EVIdleBool[S0_0,D1,64]
EVIdleBool[S0_0,D1,68]
EVIdleBool[S0_0,D1,72]
EVIdleBool[S0_0,D1,76]
EVIdleBool[S0_0,D1,80]
EVIdleBool[S0_0,D1,84]
EVIdleBool[S0_0,D1,88]
EVIdleBool[S0_0,D1,92]
EVIdleBool[S0_0,D1,96]
EVIdleBool[S0_0,D1,100]
EVIdleBool[S0_0,D1,104]
EVIdleBool[S0_0,D1,108]
EVIdleBool[S0_0,D1,112]
EVIdleBool[S0_0,D1,116]
EVIdleBool[S0_0,D1,120]
EVIdleBool[S0_0,D1,124]
EVIdleBool[S0_0,D1,128]
EVIdleBool[S0_0,D1,132]
EVIdleBool[S0_0,D1,136]
EVIdleBool[S0_0,D1,140]
EVIdleBool[S0_0,D1,144]
EVIdleBool[S0_0,D1,148]
EVIdleBool[S0_0,D1,152]
EVIdleBool[S0_0,D1,156]
EVIdleBool[S0_0,D1,160]
EVIdleBool[S0_0,D1,164]
EVIdleBool[S0_0,D1,1

EVIdleBool[S0_0,S15_0,528]
EVIdleBool[S0_0,S15_0,532]
EVIdleBool[S0_0,S15_0,536]
EVIdleBool[S0_0,S15_0,540]
EVIdleBool[S0_0,S15_0,544]
EVIdleBool[S0_0,S15_0,548]
EVIdleBool[S0_0,S15_0,552]
EVIdleBool[S0_0,S15_0,556]
EVIdleBool[S0_0,S15_0,560]
EVIdleBool[S0_0,S15_0,564]
EVIdleBool[S0_0,S15_0,568]
EVIdleBool[S0_0,S15_0,572]
EVIdleBool[S0_0,S15_0,576]
EVIdleBool[S0_0,S15_0,580]
EVIdleBool[S0_0,S15_0,584]
EVIdleBool[S0_0,S15_0,588]
EVIdleBool[S0_0,S15_0,592]
EVIdleBool[S0_0,S15_0,596]
EVIdleBool[S0_0,S15_0,600]
EVIdleBool[S0_0,S15_0,604]
EVIdleBool[S0_0,S15_0,608]
EVIdleBool[S0_0,S15_0,612]
EVIdleBool[S0_0,S15_0,616]
EVIdleBool[S0_0,S15_0,620]
EVIdleBool[S0_0,S15_0,624]
EVIdleBool[S0_0,S15_0,628]
EVIdleBool[S0_0,S15_0,632]
EVIdleBool[S0_0,S15_0,636]
EVIdleBool[S0_0,S15_0,640]
EVIdleBool[S0_0,S15_0,644]
EVIdleBool[S0_0,S15_0,648]
EVIdleBool[S0_0,S15_0,652]
EVIdleBool[S0_0,S15_0,656]
EVIdleBool[S0_0,S15_0,660]
EVIdleBool[S0_0,S15_0,664]
EVIdleBool[S0_0,S15_0,668]
EVIdleBool[S0_0,S15_0,672]
E

EVIdleBool[S0_0,C20,996]
EVIdleBool[S0_0,C20,1000]
EVIdleBool[S0_0,C20,1004]
EVIdleBool[S0_0,C20,1008]
EVIdleBool[S0_0,C20,1012]
EVIdleBool[S0_0,C20,1016]
EVIdleBool[S0_0,C20,1020]
EVIdleBool[S0_0,C20,1024]
EVIdleBool[S0_0,C20,1028]
EVIdleBool[S0_0,C20,1032]
EVIdleBool[S0_0,C20,1036]
EVIdleBool[S0_0,C20,1040]
EVIdleBool[S0_0,C20,1044]
EVIdleBool[S0_0,C20,1048]
EVIdleBool[S0_0,C20,1052]
EVIdleBool[S0_0,C20,1056]
EVIdleBool[S0_0,C20,1060]
EVIdleBool[S0_0,C20,1064]
EVIdleBool[S0_0,C20,1068]
EVIdleBool[S0_0,C20,1072]
EVIdleBool[S0_0,C20,1076]
EVIdleBool[S0_0,C20,1080]
EVIdleBool[S0_0,C20,1084]
EVIdleBool[S0_0,C20,1088]
EVIdleBool[S0_0,C20,1092]
EVIdleBool[S0_0,C20,1096]
EVIdleBool[S0_0,C20,1100]
EVIdleBool[S0_0,C20,1104]
EVIdleBool[S0_0,C20,1108]
EVIdleBool[S0_0,C20,1112]
EVIdleBool[S0_0,C20,1116]
EVIdleBool[S0_0,C20,1120]
EVIdleBool[S0_0,C20,1124]
EVIdleBool[S0_0,C20,1128]
EVIdleBool[S0_0,C20,1132]
EVIdleBool[S0_0,C20,1136]
EVIdleBool[S0_0,C20,1140]
EVIdleBool[S0_0,C20,1144]
EVIdleBool[S0

EVIdleBool[S0_0,C65,196]
EVIdleBool[S0_0,C65,200]
EVIdleBool[S0_0,C65,204]
EVIdleBool[S0_0,C65,208]
EVIdleBool[S0_0,C65,212]
EVIdleBool[S0_0,C65,216]
EVIdleBool[S0_0,C65,220]
EVIdleBool[S0_0,C65,224]
EVIdleBool[S0_0,C65,228]
EVIdleBool[S0_0,C65,232]
EVIdleBool[S0_0,C65,236]
EVIdleBool[S0_0,C65,240]
EVIdleBool[S0_0,C65,244]
EVIdleBool[S0_0,C65,248]
EVIdleBool[S0_0,C65,252]
EVIdleBool[S0_0,C65,256]
EVIdleBool[S0_0,C65,260]
EVIdleBool[S0_0,C65,264]
EVIdleBool[S0_0,C65,268]
EVIdleBool[S0_0,C65,272]
EVIdleBool[S0_0,C65,276]
EVIdleBool[S0_0,C65,280]
EVIdleBool[S0_0,C65,284]
EVIdleBool[S0_0,C65,288]
EVIdleBool[S0_0,C65,292]
EVIdleBool[S0_0,C65,296]
EVIdleBool[S0_0,C65,300]
EVIdleBool[S0_0,C65,304]
EVIdleBool[S0_0,C65,308]
EVIdleBool[S0_0,C65,312]
EVIdleBool[S0_0,C65,316]
EVIdleBool[S0_0,C65,320]
EVIdleBool[S0_0,C65,324]
EVIdleBool[S0_0,C65,328]
EVIdleBool[S0_0,C65,332]
EVIdleBool[S0_0,C65,336]
EVIdleBool[S0_0,C65,340]
EVIdleBool[S0_0,C65,344]
EVIdleBool[S0_0,C65,348]
EVIdleBool[S0_0,C65,352]


EVIdleBool[S0_0,C57,480]
EVIdleBool[S0_0,C57,484]
EVIdleBool[S0_0,C57,488]
EVIdleBool[S0_0,C57,492]
EVIdleBool[S0_0,C57,496]
EVIdleBool[S0_0,C57,500]
EVIdleBool[S0_0,C57,504]
EVIdleBool[S0_0,C57,508]
EVIdleBool[S0_0,C57,512]
EVIdleBool[S0_0,C57,516]
EVIdleBool[S0_0,C57,520]
EVIdleBool[S0_0,C57,524]
EVIdleBool[S0_0,C57,528]
EVIdleBool[S0_0,C57,532]
EVIdleBool[S0_0,C57,536]
EVIdleBool[S0_0,C57,540]
EVIdleBool[S0_0,C57,544]
EVIdleBool[S0_0,C57,548]
EVIdleBool[S0_0,C57,552]
EVIdleBool[S0_0,C57,556]
EVIdleBool[S0_0,C57,560]
EVIdleBool[S0_0,C57,564]
EVIdleBool[S0_0,C57,568]
EVIdleBool[S0_0,C57,572]
EVIdleBool[S0_0,C57,576]
EVIdleBool[S0_0,C57,580]
EVIdleBool[S0_0,C57,584]
EVIdleBool[S0_0,C57,588]
EVIdleBool[S0_0,C57,592]
EVIdleBool[S0_0,C57,596]
EVIdleBool[S0_0,C57,600]
EVIdleBool[S0_0,C57,604]
EVIdleBool[S0_0,C57,608]
EVIdleBool[S0_0,C57,612]
EVIdleBool[S0_0,C57,616]
EVIdleBool[S0_0,C57,620]
EVIdleBool[S0_0,C57,624]
EVIdleBool[S0_0,C57,628]
EVIdleBool[S0_0,C57,632]
EVIdleBool[S0_0,C57,636]


...

EVIdleBool[S15_0,S0_0,912]
EVIdleBool[S15_0,S0_0,916]
EVIdleBool[S15_0,S0_0,920]
EVIdleBool[S15_0,S0_0,924]
EVIdleBool[S15_0,S0_0,928]
EVIdleBool[S15_0,S0_0,932]
EVIdleBool[S15_0,S0_0,936]
EVIdleBool[S15_0,S0_0,940]
EVIdleBool[S15_0,S0_0,944]
EVIdleBool[S15_0,S0_0,948]
EVIdleBool[S15_0,S0_0,952]
EVIdleBool[S15_0,S0_0,956]
EVIdleBool[S15_0,S0_0,960]
EVIdleBool[S15_0,S0_0,964]
EVIdleBool[S15_0,S0_0,968]
EVIdleBool[S15_0,S0_0,972]
EVIdleBool[S15_0,S0_0,976]
EVIdleBool[S15_0,S0_0,980]
EVIdleBool[S15_0,S0_0,984]
EVIdleBool[S15_0,S0_0,988]
EVIdleBool[S15_0,S0_0,992]
EVIdleBool[S15_0,S0_0,996]
EVIdleBool[S15_0,S0_0,1000]
EVIdleBool[S15_0,S0_0,1004]
EVIdleBool[S15_0,S0_0,1008]
EVIdleBool[S15_0,S0_0,1012]
EVIdleBool[S15_0,S0_0,1016]
EVIdleBool[S15_0,S0_0,1020]
EVIdleBool[S15_0,S0_0,1024]
EVIdleBool[S15_0,S0_0,1028]
EVIdleBool[S15_0,S0_0,1032]
EVIdleBool[S15_0,S0_0,1036]
EVIdleBool[S15_0,S0_0,1040]
EVIdleBool[S15_0,S0_0,1044]
EVIdleBool[S15_0,S0_0,1048]
EVIdleBool[S15_0,S0_0,1052]
EVIdleBool[S15

EVIdleBool[S15_0,C20,1124]
EVIdleBool[S15_0,C20,1128]
EVIdleBool[S15_0,C20,1132]
EVIdleBool[S15_0,C20,1136]
EVIdleBool[S15_0,C20,1140]
EVIdleBool[S15_0,C20,1144]
EVIdleBool[S15_0,C20,1148]
EVIdleBool[S15_0,C20,1152]
EVIdleBool[S15_0,C20,1156]
EVIdleBool[S15_0,C20,1160]
EVIdleBool[S15_0,C20,1164]
EVIdleBool[S15_0,C20,1168]
EVIdleBool[S15_0,C20,1172]
EVIdleBool[S15_0,C20,1176]
EVIdleBool[S15_0,C20,1180]
EVIdleBool[S15_0,C20,1184]
EVIdleBool[S15_0,C20,1188]
EVIdleBool[S15_0,C20,1192]
EVIdleBool[S15_0,C20,1196]
EVIdleBool[S15_0,C20,1200]
EVIdleBool[S15_0,C20,1204]
EVIdleBool[S15_0,C20,1208]
EVIdleBool[S15_0,C20,1212]
EVIdleBool[S15_0,C20,1216]
EVIdleBool[S15_0,C20,1220]
EVIdleBool[S15_0,C20,1224]
EVIdleBool[S15_0,C20,1228]
EVIdleBool[S15_0,C20,1232]
EVIdleBool[S15_0,C98,0]
EVIdleBool[S15_0,C98,4]
EVIdleBool[S15_0,C98,8]
EVIdleBool[S15_0,C98,12]
EVIdleBool[S15_0,C98,16]
EVIdleBool[S15_0,C98,20]
EVIdleBool[S15_0,C98,24]
EVIdleBool[S15_0,C98,28]
EVIdleBool[S15_0,C98,32]
EVIdleBool[S15_0,C98,3

EVIdleBool[S15_0,C98,1172]
EVIdleBool[S15_0,C98,1176]
EVIdleBool[S15_0,C98,1180]
EVIdleBool[S15_0,C98,1184]
EVIdleBool[S15_0,C98,1188]
EVIdleBool[S15_0,C98,1192]
EVIdleBool[S15_0,C98,1196]
EVIdleBool[S15_0,C98,1200]
EVIdleBool[S15_0,C98,1204]
EVIdleBool[S15_0,C98,1208]
EVIdleBool[S15_0,C98,1212]
EVIdleBool[S15_0,C98,1216]
EVIdleBool[S15_0,C98,1220]
EVIdleBool[S15_0,C98,1224]
EVIdleBool[S15_0,C98,1228]
EVIdleBool[S15_0,C98,1232]
EVIdleBool[S15_0,C65,0]
EVIdleBool[S15_0,C65,4]
EVIdleBool[S15_0,C65,8]
EVIdleBool[S15_0,C65,12]
EVIdleBool[S15_0,C65,16]
EVIdleBool[S15_0,C65,20]
EVIdleBool[S15_0,C65,24]
EVIdleBool[S15_0,C65,28]
EVIdleBool[S15_0,C65,32]
EVIdleBool[S15_0,C65,36]
EVIdleBool[S15_0,C65,40]
EVIdleBool[S15_0,C65,44]
EVIdleBool[S15_0,C65,48]
EVIdleBool[S15_0,C65,52]
EVIdleBool[S15_0,C65,56]
EVIdleBool[S15_0,C65,60]
EVIdleBool[S15_0,C65,64]
EVIdleBool[S15_0,C65,68]
EVIdleBool[S15_0,C65,72]
EVIdleBool[S15_0,C65,76]
EVIdleBool[S15_0,C65,80]
EVIdleBool[S15_0,C65,84]
EVIdleBool[S15_0,C65,

EVIdleBool[S15_0,C57,36]
EVIdleBool[S15_0,C57,40]
EVIdleBool[S15_0,C57,44]
EVIdleBool[S15_0,C57,48]
EVIdleBool[S15_0,C57,52]
EVIdleBool[S15_0,C57,56]
EVIdleBool[S15_0,C57,60]
EVIdleBool[S15_0,C57,64]
EVIdleBool[S15_0,C57,68]
EVIdleBool[S15_0,C57,72]
EVIdleBool[S15_0,C57,76]
EVIdleBool[S15_0,C57,80]
EVIdleBool[S15_0,C57,84]
EVIdleBool[S15_0,C57,88]
EVIdleBool[S15_0,C57,92]
EVIdleBool[S15_0,C57,96]
EVIdleBool[S15_0,C57,100]
EVIdleBool[S15_0,C57,104]
EVIdleBool[S15_0,C57,108]
EVIdleBool[S15_0,C57,112]
EVIdleBool[S15_0,C57,116]
EVIdleBool[S15_0,C57,120]
EVIdleBool[S15_0,C57,124]
EVIdleBool[S15_0,C57,128]
EVIdleBool[S15_0,C57,132]
EVIdleBool[S15_0,C57,136]
EVIdleBool[S15_0,C57,140]
EVIdleBool[S15_0,C57,144]
EVIdleBool[S15_0,C57,148]
EVIdleBool[S15_0,C57,152]
EVIdleBool[S15_0,C57,156]
EVIdleBool[S15_0,C57,160]
EVIdleBool[S15_0,C57,164]
EVIdleBool[S15_0,C57,168]
EVIdleBool[S15_0,C57,172]
EVIdleBool[S15_0,C57,176]
EVIdleBool[S15_0,C57,180]
EVIdleBool[S15_0,C57,184]
EVIdleBool[S15_0,C57,188]
EV

EVIdleBool[S15_0,C24,204]
EVIdleBool[S15_0,C24,208]
EVIdleBool[S15_0,C24,212]
EVIdleBool[S15_0,C24,216]
EVIdleBool[S15_0,C24,220]
EVIdleBool[S15_0,C24,224]
EVIdleBool[S15_0,C24,228]
EVIdleBool[S15_0,C24,232]
EVIdleBool[S15_0,C24,236]
EVIdleBool[S15_0,C24,240]
EVIdleBool[S15_0,C24,244]
EVIdleBool[S15_0,C24,248]
EVIdleBool[S15_0,C24,252]
EVIdleBool[S15_0,C24,256]
EVIdleBool[S15_0,C24,260]
EVIdleBool[S15_0,C24,264]
EVIdleBool[S15_0,C24,268]
EVIdleBool[S15_0,C24,272]
EVIdleBool[S15_0,C24,276]
EVIdleBool[S15_0,C24,280]
EVIdleBool[S15_0,C24,284]
EVIdleBool[S15_0,C24,288]
EVIdleBool[S15_0,C24,292]
EVIdleBool[S15_0,C24,296]
EVIdleBool[S15_0,C24,300]
EVIdleBool[S15_0,C24,304]
EVIdleBool[S15_0,C24,308]
EVIdleBool[S15_0,C24,312]
EVIdleBool[S15_0,C24,316]
EVIdleBool[S15_0,C24,320]
EVIdleBool[S15_0,C24,324]
EVIdleBool[S15_0,C24,328]
EVIdleBool[S15_0,C24,332]
EVIdleBool[S15_0,C24,336]
EVIdleBool[S15_0,C24,340]
EVIdleBool[S15_0,C24,344]
EVIdleBool[S15_0,C24,348]
EVIdleBool[S15_0,C24,352]
EVIdleBool[S

In [45]:
for s in m.instance.S_:
    for j in m.instance.V1_:
        if s != j:
            for t in m.instance.T:
                ArcOffBoolVar = m.instance.ArcOffBool[s,j]
                ArcOffBoolVal = ArcOffBoolVar.value
                
                EVIdleBoolVar = m.instance.EVIdleBool[s,j,t]
                EVIdleBoolVal = EVIdleBoolVar.value
                
                EVChargeDischargeBoolVar = m.instance.EVChargeDischargeBool[s,j,t]
                EVChargeDischargeBoolVal = EVChargeDischargeBoolVar.value
                
                if ArcOffBoolVal != EVIdleBoolVal and ArcOffBoolVal is True:
                    print('ArcOffBool : {} --> Val: {}'.format(ArcOffBoolVar, ArcOffBoolVal))
                    print('EVIdleBool : {} --> Val: {}'.format(EVIdleBoolVar, EVIdleBoolVal))
                    print('EVChargeDischargeBool : {} --> Val: {}'.format(EVChargeDischargeBoolVar, EVChargeDischargeBoolVal))
                    print('----------------------------------------\n')

In [46]:
for idx in m.instance.xkappa:
#     print(idx)
    if m.instance.xkappa[idx].value > 0:
        m.instance.xkappa[idx].pprint()

{Member of xkappa} : Size=4944, Index=xkappa_index
    Key                  : Lower : Value : Upper : Fixed : Stale : Domain
    ('S0_0', 'C98', 172) :     0 :   1.0 :     1 : False : False : Boolean
{Member of xkappa} : Size=4944, Index=xkappa_index
    Key                  : Lower : Value : Upper : Fixed : Stale : Domain
    ('S0_0', 'C98', 184) :     0 :   1.0 :     1 : False : False : Boolean
{Member of xkappa} : Size=4944, Index=xkappa_index
    Key                  : Lower : Value : Upper : Fixed : Stale : Domain
    ('S0_0', 'C98', 196) :     0 :   1.0 :     1 : False : False : Boolean
{Member of xkappa} : Size=4944, Index=xkappa_index
    Key                  : Lower : Value : Upper : Fixed : Stale : Domain
    ('S0_0', 'C98', 208) :     0 :   1.0 :     1 : False : False : Boolean
{Member of xkappa} : Size=4944, Index=xkappa_index
    Key                  : Lower : Value : Upper : Fixed : Stale : Domain
    ('S0_0', 'C98', 212) :     0 :   1.0 :     1 : False : False : Boolean


{Member of xkappa} : Size=4944, Index=xkappa_index
    Key                    : Lower : Value : Upper : Fixed : Stale : Domain
    ('S15_0', 'C57', 1020) :     0 :   1.0 :     1 : False : False : Boolean
{Member of xkappa} : Size=4944, Index=xkappa_index
    Key                    : Lower : Value : Upper : Fixed : Stale : Domain
    ('S15_0', 'C57', 1024) :     0 :   1.0 :     1 : False : False : Boolean
{Member of xkappa} : Size=4944, Index=xkappa_index
    Key                    : Lower : Value : Upper : Fixed : Stale : Domain
    ('S15_0', 'C57', 1028) :     0 :   1.0 :     1 : False : False : Boolean
{Member of xkappa} : Size=4944, Index=xkappa_index
    Key                    : Lower : Value : Upper : Fixed : Stale : Domain
    ('S15_0', 'C57', 1032) :     0 :   1.0 :     1 : False : False : Boolean
{Member of xkappa} : Size=4944, Index=xkappa_index
    Key                    : Lower : Value : Upper : Fixed : Stale : Domain
    ('S15_0', 'C57', 1036) :     0 :   1.0 :     1 : Fals

In [47]:
for idx in m.instance.xp:
    print(idx)
    if m.instance.xp[idx].value > 0:
        m.instance.xp[idx].pprint()

('S0_0', 'D1', 0)
('S0_0', 'D1', 4)
('S0_0', 'D1', 8)
('S0_0', 'D1', 12)
('S0_0', 'D1', 16)
('S0_0', 'D1', 20)
('S0_0', 'D1', 24)
('S0_0', 'D1', 28)
('S0_0', 'D1', 32)
('S0_0', 'D1', 36)
('S0_0', 'D1', 40)
('S0_0', 'D1', 44)
('S0_0', 'D1', 48)
('S0_0', 'D1', 52)
('S0_0', 'D1', 56)
('S0_0', 'D1', 60)
('S0_0', 'D1', 64)
('S0_0', 'D1', 68)
('S0_0', 'D1', 72)
('S0_0', 'D1', 76)
('S0_0', 'D1', 80)
('S0_0', 'D1', 84)
('S0_0', 'D1', 88)
('S0_0', 'D1', 92)
('S0_0', 'D1', 96)
('S0_0', 'D1', 100)
('S0_0', 'D1', 104)
('S0_0', 'D1', 108)
('S0_0', 'D1', 112)
('S0_0', 'D1', 116)
('S0_0', 'D1', 120)
('S0_0', 'D1', 124)
('S0_0', 'D1', 128)
('S0_0', 'D1', 132)
('S0_0', 'D1', 136)
('S0_0', 'D1', 140)
('S0_0', 'D1', 144)
('S0_0', 'D1', 148)
('S0_0', 'D1', 152)
('S0_0', 'D1', 156)
('S0_0', 'D1', 160)
('S0_0', 'D1', 164)
('S0_0', 'D1', 168)
('S0_0', 'D1', 172)
('S0_0', 'D1', 176)
('S0_0', 'D1', 180)
('S0_0', 'D1', 184)
('S0_0', 'D1', 188)
('S0_0', 'D1', 192)
('S0_0', 'D1', 196)
('S0_0', 'D1', 200)
('S0_0',

('S0_0', 'S0_0', 744)
('S0_0', 'S0_0', 748)
('S0_0', 'S0_0', 752)
{Member of xp} : Size=4944, Index=xp_index
    Key                   : Lower        : Value       : Upper       : Fixed : Stale : Domain
    ('S0_0', 'S0_0', 752) : -0.288184438 : 0.288184438 : 0.288184438 : False : False :  Reals
('S0_0', 'S0_0', 756)
{Member of xp} : Size=4944, Index=xp_index
    Key                   : Lower        : Value       : Upper       : Fixed : Stale : Domain
    ('S0_0', 'S0_0', 756) : -0.288184438 : 0.288184438 : 0.288184438 : False : False :  Reals
('S0_0', 'S0_0', 760)
('S0_0', 'S0_0', 764)
('S0_0', 'S0_0', 768)
{Member of xp} : Size=4944, Index=xp_index
    Key                   : Lower        : Value       : Upper       : Fixed : Stale : Domain
    ('S0_0', 'S0_0', 768) : -0.288184438 : 0.288184438 : 0.288184438 : False : False :  Reals
('S0_0', 'S0_0', 772)
('S0_0', 'S0_0', 776)
{Member of xp} : Size=4944, Index=xp_index
    Key                   : Lower        : Value       : Upper    

('S0_0', 'S15_0', 904)
('S0_0', 'S15_0', 908)
('S0_0', 'S15_0', 912)
('S0_0', 'S15_0', 916)
('S0_0', 'S15_0', 920)
('S0_0', 'S15_0', 924)
('S0_0', 'S15_0', 928)
('S0_0', 'S15_0', 932)
('S0_0', 'S15_0', 936)
('S0_0', 'S15_0', 940)
('S0_0', 'S15_0', 944)
('S0_0', 'S15_0', 948)
('S0_0', 'S15_0', 952)
('S0_0', 'S15_0', 956)
('S0_0', 'S15_0', 960)
('S0_0', 'S15_0', 964)
('S0_0', 'S15_0', 968)
('S0_0', 'S15_0', 972)
('S0_0', 'S15_0', 976)
('S0_0', 'S15_0', 980)
('S0_0', 'S15_0', 984)
('S0_0', 'S15_0', 988)
('S0_0', 'S15_0', 992)
('S0_0', 'S15_0', 996)
('S0_0', 'S15_0', 1000)
('S0_0', 'S15_0', 1004)
('S0_0', 'S15_0', 1008)
('S0_0', 'S15_0', 1012)
('S0_0', 'S15_0', 1016)
('S0_0', 'S15_0', 1020)
('S0_0', 'S15_0', 1024)
('S0_0', 'S15_0', 1028)
('S0_0', 'S15_0', 1032)
('S0_0', 'S15_0', 1036)
('S0_0', 'S15_0', 1040)
('S0_0', 'S15_0', 1044)
('S0_0', 'S15_0', 1048)
('S0_0', 'S15_0', 1052)
('S0_0', 'S15_0', 1056)
('S0_0', 'S15_0', 1060)
('S0_0', 'S15_0', 1064)
('S0_0', 'S15_0', 1068)
('S0_0', 'S15_0'

{Member of xp} : Size=4944, Index=xp_index
    Key                  : Lower        : Value       : Upper       : Fixed : Stale : Domain
    ('S0_0', 'C98', 268) : -0.288184438 : 0.288184438 : 0.288184438 : False : False :  Reals
('S0_0', 'C98', 272)
{Member of xp} : Size=4944, Index=xp_index
    Key                  : Lower        : Value       : Upper       : Fixed : Stale : Domain
    ('S0_0', 'C98', 272) : -0.288184438 : 0.288184438 : 0.288184438 : False : False :  Reals
('S0_0', 'C98', 276)
{Member of xp} : Size=4944, Index=xp_index
    Key                  : Lower        : Value       : Upper       : Fixed : Stale : Domain
    ('S0_0', 'C98', 276) : -0.288184438 : 0.288184438 : 0.288184438 : False : False :  Reals
('S0_0', 'C98', 280)
{Member of xp} : Size=4944, Index=xp_index
    Key                  : Lower        : Value              : Upper       : Fixed : Stale : Domain
    ('S0_0', 'C98', 280) : -0.288184438 : 0.2717321138072002 : 0.288184438 : False : False :  Reals
('S0_0'

('S0_0', 'C98', 1092)
('S0_0', 'C98', 1096)
('S0_0', 'C98', 1100)
('S0_0', 'C98', 1104)
('S0_0', 'C98', 1108)
('S0_0', 'C98', 1112)
('S0_0', 'C98', 1116)
('S0_0', 'C98', 1120)
('S0_0', 'C98', 1124)
('S0_0', 'C98', 1128)
('S0_0', 'C98', 1132)
('S0_0', 'C98', 1136)
('S0_0', 'C98', 1140)
('S0_0', 'C98', 1144)
('S0_0', 'C98', 1148)
('S0_0', 'C98', 1152)
('S0_0', 'C98', 1156)
('S0_0', 'C98', 1160)
('S0_0', 'C98', 1164)
('S0_0', 'C98', 1168)
('S0_0', 'C98', 1172)
('S0_0', 'C98', 1176)
('S0_0', 'C98', 1180)
('S0_0', 'C98', 1184)
('S0_0', 'C98', 1188)
('S0_0', 'C98', 1192)
('S0_0', 'C98', 1196)
('S0_0', 'C98', 1200)
('S0_0', 'C98', 1204)
('S0_0', 'C98', 1208)
('S0_0', 'C98', 1212)
('S0_0', 'C98', 1216)
('S0_0', 'C98', 1220)
('S0_0', 'C98', 1224)
('S0_0', 'C98', 1228)
('S0_0', 'C98', 1232)
('S0_0', 'C65', 0)
('S0_0', 'C65', 4)
('S0_0', 'C65', 8)
('S0_0', 'C65', 12)
('S0_0', 'C65', 16)
('S0_0', 'C65', 20)
('S0_0', 'C65', 24)
('S0_0', 'C65', 28)
('S0_0', 'C65', 32)
('S0_0', 'C65', 36)
('S0_0', 'C

...

{Member of xp} : Size=4944, Index=xp_index
    Key                     : Lower        : Value       : Upper       : Fixed : Stale : Domain
    ('S15_0', 'S15_0', 236) : -0.288184438 : 0.288184438 : 0.288184438 : False : False :  Reals
('S15_0', 'S15_0', 240)
{Member of xp} : Size=4944, Index=xp_index
    Key                     : Lower        : Value       : Upper       : Fixed : Stale : Domain
    ('S15_0', 'S15_0', 240) : -0.288184438 : 0.288184438 : 0.288184438 : False : False :  Reals
('S15_0', 'S15_0', 244)
{Member of xp} : Size=4944, Index=xp_index
    Key                     : Lower        : Value                 : Upper       : Fixed : Stale : Domain
    ('S15_0', 'S15_0', 244) : -0.288184438 : 0.0011334662866442358 : 0.288184438 : False : False :  Reals
('S15_0', 'S15_0', 248)
('S15_0', 'S15_0', 252)
('S15_0', 'S15_0', 256)
('S15_0', 'S15_0', 260)
('S15_0', 'S15_0', 264)
('S15_0', 'S15_0', 268)
('S15_0', 'S15_0', 272)
('S15_0', 'S15_0', 276)
('S15_0', 'S15_0', 280)
('S15_0', '

{Member of xp} : Size=4944, Index=xp_index
    Key                     : Lower        : Value       : Upper       : Fixed : Stale : Domain
    ('S15_0', 'S15_0', 988) : -0.288184438 : 0.288184438 : 0.288184438 : False : False :  Reals
('S15_0', 'S15_0', 992)
{Member of xp} : Size=4944, Index=xp_index
    Key                     : Lower        : Value       : Upper       : Fixed : Stale : Domain
    ('S15_0', 'S15_0', 992) : -0.288184438 : 0.288184438 : 0.288184438 : False : False :  Reals
('S15_0', 'S15_0', 996)
('S15_0', 'S15_0', 1000)
('S15_0', 'S15_0', 1004)
('S15_0', 'S15_0', 1008)
('S15_0', 'S15_0', 1012)
('S15_0', 'S15_0', 1016)
('S15_0', 'S15_0', 1020)
{Member of xp} : Size=4944, Index=xp_index
    Key                      : Lower        : Value       : Upper       : Fixed : Stale : Domain
    ('S15_0', 'S15_0', 1020) : -0.288184438 : 0.288184438 : 0.288184438 : False : False :  Reals
('S15_0', 'S15_0', 1024)
('S15_0', 'S15_0', 1028)
('S15_0', 'S15_0', 1032)
{Member of xp} : Siz

('S15_0', 'C20', 1096)
('S15_0', 'C20', 1100)
('S15_0', 'C20', 1104)
('S15_0', 'C20', 1108)
('S15_0', 'C20', 1112)
('S15_0', 'C20', 1116)
('S15_0', 'C20', 1120)
('S15_0', 'C20', 1124)
('S15_0', 'C20', 1128)
('S15_0', 'C20', 1132)
('S15_0', 'C20', 1136)
('S15_0', 'C20', 1140)
('S15_0', 'C20', 1144)
('S15_0', 'C20', 1148)
('S15_0', 'C20', 1152)
('S15_0', 'C20', 1156)
('S15_0', 'C20', 1160)
('S15_0', 'C20', 1164)
('S15_0', 'C20', 1168)
('S15_0', 'C20', 1172)
('S15_0', 'C20', 1176)
('S15_0', 'C20', 1180)
('S15_0', 'C20', 1184)
('S15_0', 'C20', 1188)
('S15_0', 'C20', 1192)
('S15_0', 'C20', 1196)
('S15_0', 'C20', 1200)
('S15_0', 'C20', 1204)
('S15_0', 'C20', 1208)
('S15_0', 'C20', 1212)
('S15_0', 'C20', 1216)
('S15_0', 'C20', 1220)
('S15_0', 'C20', 1224)
('S15_0', 'C20', 1228)
('S15_0', 'C20', 1232)
('S15_0', 'C98', 0)
('S15_0', 'C98', 4)
('S15_0', 'C98', 8)
('S15_0', 'C98', 12)
('S15_0', 'C98', 16)
('S15_0', 'C98', 20)
('S15_0', 'C98', 24)
('S15_0', 'C98', 28)
('S15_0', 'C98', 32)
('S15_0',

{Member of xp} : Size=4944, Index=xp_index
    Key                   : Lower        : Value       : Upper       : Fixed : Stale : Domain
    ('S15_0', 'C57', 952) : -0.288184438 : 0.288184438 : 0.288184438 : False : False :  Reals
('S15_0', 'C57', 956)
{Member of xp} : Size=4944, Index=xp_index
    Key                   : Lower        : Value       : Upper       : Fixed : Stale : Domain
    ('S15_0', 'C57', 956) : -0.288184438 : 0.288184438 : 0.288184438 : False : False :  Reals
('S15_0', 'C57', 960)
('S15_0', 'C57', 964)
{Member of xp} : Size=4944, Index=xp_index
    Key                   : Lower        : Value       : Upper       : Fixed : Stale : Domain
    ('S15_0', 'C57', 964) : -0.288184438 : 0.288184438 : 0.288184438 : False : False :  Reals
('S15_0', 'C57', 968)
{Member of xp} : Size=4944, Index=xp_index
    Key                   : Lower        : Value       : Upper       : Fixed : Stale : Domain
    ('S15_0', 'C57', 968) : -0.288184438 : 0.288184438 : 0.288184438 : False : Fal

('S15_0', 'C24', 316)
('S15_0', 'C24', 320)
('S15_0', 'C24', 324)
('S15_0', 'C24', 328)
('S15_0', 'C24', 332)
('S15_0', 'C24', 336)
('S15_0', 'C24', 340)
('S15_0', 'C24', 344)
('S15_0', 'C24', 348)
('S15_0', 'C24', 352)
('S15_0', 'C24', 356)
('S15_0', 'C24', 360)
('S15_0', 'C24', 364)
('S15_0', 'C24', 368)
('S15_0', 'C24', 372)
('S15_0', 'C24', 376)
('S15_0', 'C24', 380)
('S15_0', 'C24', 384)
('S15_0', 'C24', 388)
('S15_0', 'C24', 392)
('S15_0', 'C24', 396)
('S15_0', 'C24', 400)
('S15_0', 'C24', 404)
('S15_0', 'C24', 408)
('S15_0', 'C24', 412)
('S15_0', 'C24', 416)
('S15_0', 'C24', 420)
('S15_0', 'C24', 424)
('S15_0', 'C24', 428)
('S15_0', 'C24', 432)
('S15_0', 'C24', 436)
('S15_0', 'C24', 440)
('S15_0', 'C24', 444)
('S15_0', 'C24', 448)
('S15_0', 'C24', 452)
('S15_0', 'C24', 456)
('S15_0', 'C24', 460)
('S15_0', 'C24', 464)
('S15_0', 'C24', 468)
('S15_0', 'C24', 472)
('S15_0', 'C24', 476)
('S15_0', 'C24', 480)
('S15_0', 'C24', 484)
('S15_0', 'C24', 488)
('S15_0', 'C24', 492)
('S15_0', 

In [135]:
for t in m.instance.T:
    var = m.instance.EVChargeDischarge['S0_0', 'C20', t].indicator_var.value
    if var > 0:
        print(var)
        print('[S0_0, C20, {}] --> {}'.format(t, var))
    

In [34]:
m.instance.EVIdleBool['S0_0', 'C98', 796].pprint()

{Member of EVIdleBool} : Size=4944, Index=EVIdleBool_index
    Key                  : Value : Fixed : Stale
    ('S0_0', 'C98', 796) :  True : False : False


In [101]:
# routes

In [112]:
x = getattr(m.instance, 'xgamma')
# keys, values = zip(*x.get_values().items())
x_val = x.extract_values()
active_arcs = [n for n in list(x_val.items()) if n[1] == 1.0]
active_arcs

[(('D0', 'C65'), 1.0),
 (('D0', 'C24'), 1.0),
 (('S0_0', 'C98'), 1.0),
 (('C20', 'S0_0'), 1.0),
 (('C98', 'D1'), 1.0),
 (('C65', 'C57'), 1.0),
 (('C57', 'D1'), 1.0),
 (('C24', 'C20'), 1.0)]

In [118]:
x = getattr(m.instance, 'xkappa')
# keys, values = zip(*x.get_values().items())
x_val = x.extract_values()
active_arcs = [n for n in list(x_val.items()) if n[1] == 1.0]
active_arcs

[(('S0_0', 796), 1.0),
 (('S0_0', 800), 1.0),
 (('S0_0', 848), 1.0),
 (('S0_0', 932), 1.0),
 (('S0_0', 996), 1.0),
 (('S0_0', 1040), 1.0),
 (('S0_0', 1068), 1.0),
 (('S0_0', 1076), 1.0),
 (('S0_0', 1096), 1.0),
 (('S0_0', 1164), 1.0),
 (('S0_0', 1172), 1.0),
 (('S0_0', 1212), 1.0),
 (('S0_0', 1232), 1.0)]

In [18]:
# m.instance.xw.pprint()

In [82]:
x = getattr(m.instance, 'xp')
# keys, values = zip(*x.get_values().items())
x_val = x.extract_values()
active_arcs = [n for n in list(x_val.items()) if n[1] > 0]
active_arcs

[]

In [70]:
m.instance.tB.pprint()

tB : Time window end time at node i
    Size=9, Index=V01_, Domain=Any, Default=None, Mutable=True
    Key   : Value
      C20 :  1136
      C24 :  1131
      C57 :  1063
      C65 :   139
      C98 :  1115
       D0 :  1236
       D1 :  1236
     S0_0 :  1236
    S15_0 :  1236


In [29]:
m.instance.ArcOn.pprint()

ArcOn : Size=64, Index=ArcOn_index, Active=True
    ArcOn[C20,C20] : Active=True
        1 Var Declarations
            indicator_var : Size=1, Index=None
                Key  : Lower : Value : Upper : Fixed : Stale : Domain
                None :     0 :  None :     1 : False :  True : Binary

        1 Declarations: indicator_var
    ArcOn[C20,C24] : Active=False
        1 Var Declarations
            indicator_var : Size=1, Index=None
                Key  : Lower : Value : Upper : Fixed : Stale : Domain
                None :     0 :   1.0 :     1 : False : False : Binary

        4 Constraint Declarations
            constraint_energy_customer : Energy transition for each EV while at customer node i and traveling across edge (i, j)
                Size=1, Index=None, Active=False
                Key  : Lower : Body                        : Upper : Active
                None :  -Inf : xa[C24] - (xa[C20] - r*5.0) :   0.0 :  False
            constraint_payload : Vehicles must unload

                Key  : Lower : Body                          : Upper : Active
                None :  -Inf : xq[S0_0] - (xq[C98] - q[C98]) :   0.0 :  False
            constraint_time_customer : Service time for each vehicle doing delivery at each customer node
                Size=1, Index=None, Active=False
                Key  : Lower : Body                                                                   : Upper : Active
                None :  -Inf : xw[C98] + (tS[C98] + 30.805843601498726/v + tQ[C98]*q[C98]) - xw[S0_0] :   0.0 :  False
            constraint_xgamma : Arc must be activated
                Size=1, Index=None, Active=False
                Key  : Lower : Body             : Upper : Active
                None :   1.0 : xgamma[C98,S0_0] :   1.0 :  False

        5 Declarations: indicator_var constraint_xgamma constraint_time_customer constraint_energy_customer constraint_payload
    ArcOn[C98,S15_0] : Active=False
        1 Var Declarations
            indicator_var :

                Key  : Lower : Body                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                     

                Key  : Lower : Body                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                     

    ArcOn[S0_0,D1] : Active=False
        1 Var Declarations
            indicator_var : Size=1, Index=None
                Key  : Lower : Value : Upper : Fixed : Stale : Domain
                None :     0 :  -0.0 :     1 : False : False : Binary

        4 Constraint Declarations
            constraint_energy_station : Energy transition for each EV while at an intermediate charging station node i and traveling across edge (i, j)
                Size=1, Index=None, Active=False
                Key  : Lower : Body                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                 

...

                Key  : Lower : Body                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                     

                Key  : Lower : Body                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                     

                Key  : Lower : Body                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                     

                Key  : Lower : Body                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                     

    ArcOn[S15_0,S15_0] : Active=True
        1 Var Declarations
            indicator_var : Size=1, Index=None
                Key  : Lower : Value : Upper : Fixed : Stale : Domain
                None :     0 :  None :     1 : False :  True : Binary

        1 Declarations: indicator_var


In [15]:
m.instance.ArcOnThen_.pprint()

ArcOnThen_ : Size=3708, Index=ArcOnThen__index, Active=True
    Key                    : Body                                                                            : Active
        ('S0_0', 'C20', 0) :          ArcOnBool[S0_0,C20] --> EVDischargeBool[S0_0,0] ⊻ EVChargeBool[S0_0,0] :   True
        ('S0_0', 'C20', 4) :          ArcOnBool[S0_0,C20] --> EVDischargeBool[S0_0,4] ⊻ EVChargeBool[S0_0,4] :   True
        ('S0_0', 'C20', 8) :          ArcOnBool[S0_0,C20] --> EVDischargeBool[S0_0,8] ⊻ EVChargeBool[S0_0,8] :   True
       ('S0_0', 'C20', 12) :        ArcOnBool[S0_0,C20] --> EVDischargeBool[S0_0,12] ⊻ EVChargeBool[S0_0,12] :   True
       ('S0_0', 'C20', 16) :        ArcOnBool[S0_0,C20] --> EVDischargeBool[S0_0,16] ⊻ EVChargeBool[S0_0,16] :   True
       ('S0_0', 'C20', 20) :        ArcOnBool[S0_0,C20] --> EVDischargeBool[S0_0,20] ⊻ EVChargeBool[S0_0,20] :   True
       ('S0_0', 'C20', 24) :        ArcOnBool[S0_0,C20] --> EVDischargeBool[S0_0,24] ⊻ EVChargeBool[S0_0,24] :   T

       ('S0_0', 'D1', 456) :       ArcOnBool[S0_0,D1] --> EVDischargeBool[S0_0,456] ⊻ EVChargeBool[S0_0,456] :   True
       ('S0_0', 'D1', 460) :       ArcOnBool[S0_0,D1] --> EVDischargeBool[S0_0,460] ⊻ EVChargeBool[S0_0,460] :   True
       ('S0_0', 'D1', 464) :       ArcOnBool[S0_0,D1] --> EVDischargeBool[S0_0,464] ⊻ EVChargeBool[S0_0,464] :   True
       ('S0_0', 'D1', 468) :       ArcOnBool[S0_0,D1] --> EVDischargeBool[S0_0,468] ⊻ EVChargeBool[S0_0,468] :   True
       ('S0_0', 'D1', 472) :       ArcOnBool[S0_0,D1] --> EVDischargeBool[S0_0,472] ⊻ EVChargeBool[S0_0,472] :   True
       ('S0_0', 'D1', 476) :       ArcOnBool[S0_0,D1] --> EVDischargeBool[S0_0,476] ⊻ EVChargeBool[S0_0,476] :   True
       ('S0_0', 'D1', 480) :       ArcOnBool[S0_0,D1] --> EVDischargeBool[S0_0,480] ⊻ EVChargeBool[S0_0,480] :   True
       ('S0_0', 'D1', 484) :       ArcOnBool[S0_0,D1] --> EVDischargeBool[S0_0,484] ⊻ EVChargeBool[S0_0,484] :   True
       ('S0_0', 'D1', 488) :       ArcOnBool[S0_0,D1] --

      ('S15_0', 'C98', 40) :     ArcOnBool[S15_0,C98] --> EVDischargeBool[S15_0,40] ⊻ EVChargeBool[S15_0,40] :   True
      ('S15_0', 'C98', 44) :     ArcOnBool[S15_0,C98] --> EVDischargeBool[S15_0,44] ⊻ EVChargeBool[S15_0,44] :   True
      ('S15_0', 'C98', 48) :     ArcOnBool[S15_0,C98] --> EVDischargeBool[S15_0,48] ⊻ EVChargeBool[S15_0,48] :   True
      ('S15_0', 'C98', 52) :     ArcOnBool[S15_0,C98] --> EVDischargeBool[S15_0,52] ⊻ EVChargeBool[S15_0,52] :   True
      ('S15_0', 'C98', 56) :     ArcOnBool[S15_0,C98] --> EVDischargeBool[S15_0,56] ⊻ EVChargeBool[S15_0,56] :   True
      ('S15_0', 'C98', 60) :     ArcOnBool[S15_0,C98] --> EVDischargeBool[S15_0,60] ⊻ EVChargeBool[S15_0,60] :   True
      ('S15_0', 'C98', 64) :     ArcOnBool[S15_0,C98] --> EVDischargeBool[S15_0,64] ⊻ EVChargeBool[S15_0,64] :   True
      ('S15_0', 'C98', 68) :     ArcOnBool[S15_0,C98] --> EVDischargeBool[S15_0,68] ⊻ EVChargeBool[S15_0,68] :   True
      ('S15_0', 'C98', 72) :     ArcOnBool[S15_0,C98] --

In [49]:
m.instance.E.pprint()

E : Graph edges
    Size=1, Index=None, Ordered=Insertion
    Key  : Dimen : Domain   : Size : Members
    None :     2 : E_domain :   57 : {('D0', 'D1'), ('D0', 'S0_0'), ('D0', 'S15_0'), ('D0', 'C20'), ('D0', 'C98'), ('D0', 'C65'), ('D0', 'C57'), ('D0', 'C24'), ('S0_0', 'D1'), ('S0_0', 'S15_0'), ('S0_0', 'C20'), ('S0_0', 'C98'), ('S0_0', 'C65'), ('S0_0', 'C57'), ('S0_0', 'C24'), ('S15_0', 'D1'), ('S15_0', 'S0_0'), ('S15_0', 'C20'), ('S15_0', 'C98'), ('S15_0', 'C65'), ('S15_0', 'C57'), ('S15_0', 'C24'), ('C20', 'D1'), ('C20', 'S0_0'), ('C20', 'S15_0'), ('C20', 'C98'), ('C20', 'C65'), ('C20', 'C57'), ('C20', 'C24'), ('C98', 'D1'), ('C98', 'S0_0'), ('C98', 'S15_0'), ('C98', 'C20'), ('C98', 'C65'), ('C98', 'C57'), ('C98', 'C24'), ('C65', 'D1'), ('C65', 'S0_0'), ('C65', 'S15_0'), ('C65', 'C20'), ('C65', 'C98'), ('C65', 'C57'), ('C65', 'C24'), ('C57', 'D1'), ('C57', 'S0_0'), ('C57', 'S15_0'), ('C57', 'C20'), ('C57', 'C98'), ('C57', 'C65'), ('C57', 'C24'), ('C24', 'D1'), ('C24', 'S0_0'), ('C

In [59]:
for idx in m.instance.E:
    print(idx)
    if idx == ('D0', 'D1'):
        m.instance.ArcOn[idx].indicator_var.pprint()

('D0', 'D1')
indicator_var : Size=1, Index=None
    Key  : Lower : Value : Upper : Fixed : Stale : Domain
    None :     0 :  -0.0 :     1 : False : False : Binary
('D0', 'S0_0')
('D0', 'S15_0')
('D0', 'C20')
('D0', 'C98')
('D0', 'C65')
('D0', 'C57')
('D0', 'C24')
('S0_0', 'D1')
('S0_0', 'S15_0')
('S0_0', 'C20')
('S0_0', 'C98')
('S0_0', 'C65')
('S0_0', 'C57')
('S0_0', 'C24')
('S15_0', 'D1')
('S15_0', 'S0_0')
('S15_0', 'C20')
('S15_0', 'C98')
('S15_0', 'C65')
('S15_0', 'C57')
('S15_0', 'C24')
('C20', 'D1')
('C20', 'S0_0')
('C20', 'S15_0')
('C20', 'C98')
('C20', 'C65')
('C20', 'C57')
('C20', 'C24')
('C98', 'D1')
('C98', 'S0_0')
('C98', 'S15_0')
('C98', 'C20')
('C98', 'C65')
('C98', 'C57')
('C98', 'C24')
('C65', 'D1')
('C65', 'S0_0')
('C65', 'S15_0')
('C65', 'C20')
('C65', 'C98')
('C65', 'C57')
('C65', 'C24')
('C57', 'D1')
('C57', 'S0_0')
('C57', 'S15_0')
('C57', 'C20')
('C57', 'C98')
('C57', 'C65')
('C57', 'C24')
('C24', 'D1')
('C24', 'S0_0')
('C24', 'S15_0')
('C24', 'C20')
('C24', 'C98'

In [ ]:
m.instance.ArcOn

In [26]:
var_list = ['xgamma', 'xw', 'xq', 'xa']
x = merge_variable_results(m, var_list)
x[x['state']>0].sort_values(['route', 'xw'])

NameError: name 'merge_variable_results' is not defined

In [8]:
x = getattr(m.instance, 'xgamma')
# keys, values = zip(*x.get_values().items())
x_val = x.extract_values()
active_arcs = [n for n in list(x_val.items()) if n[1] == 1.0]
active_arcs

[(('D0', 'C1'), 1.0),
 (('D0', 'C5'), 1.0),
 (('S3', 'C71'), 1.0),
 (('C71', 'D1'), 1.0),
 (('C1', 'S3'), 1.0),
 (('C5', 'C99'), 1.0),
 (('C87', 'D1'), 1.0),
 (('C99', 'C87'), 1.0)]

In [101]:
# m.instance.constraint_energy_customer.pprint()

In [9]:
m.instance.ArcOn.pprint()

ArcOn : Size=81, Index=ArcOn_index, Active=True
    ArcOn[C1,C1] : Active=True
        1 Var Declarations
            indicator_var : Size=1, Index=None
                Key  : Lower : Value : Upper : Fixed : Stale : Domain
                None :     0 :  None :     1 : False :  True : Binary

        1 Declarations: indicator_var
    ArcOn[C1,C5] : Active=False
        1 Var Declarations
            indicator_var : Size=1, Index=None
                Key  : Lower : Value : Upper : Fixed : Stale : Domain
                None :     0 :  -0.0 :     1 : False : False : Binary

        5 Constraint Declarations
            constraint_energy_customer : Size=1, Index=None, Active=False
                Key  : Lower : Body   : Upper                       : Active
                None :   0.0 : xa[C5] : xa[C1] - 32.202484376209235 :  False
            constraint_node_time_window : Size=1, Index=None, Active=False
                Key  : Lower : Body   : Upper : Active
                None :  36.0 

                Key  : Lower : Body                       : Upper  : Active
                None :   0.0 : xw[C99] + 27.4928556845359 : xw[S0] :  False
            constraint_xgamma : Size=1, Index=None, Active=False
                Key  : Lower : Body           : Upper : Active
                None :   1.0 : xgamma[C99,S0] :   1.0 :  False

        6 Declarations: indicator_var constraint_xgamma constraint_node_time_window constraint_payload constraint_time_customer constraint_energy_customer
    ArcOn[C99,S3] : Active=False
        1 Var Declarations
            indicator_var : Size=1, Index=None
                Key  : Lower : Value : Upper : Fixed : Stale : Domain
                None :     0 :   0.0 :     1 : False : False : Binary

        5 Constraint Declarations
            constraint_energy_customer : Size=1, Index=None, Active=False
                Key  : Lower : Body   : Upper                       : Active
                None :   0.0 : xa[S3] : xa[C99] - 44.04543109109048 

In [29]:
m.instance.ArcOn['C71', 'C1'].pprint()

{Member of ArcOn} : Size=81, Index=ArcOn_index, Active=True
    ArcOn[C71,C1] : Active=False
        1 Var Declarations
            indicator_var : Size=1, Index=None
                Key  : Lower : Value : Upper : Fixed : Stale : Domain
                None :     0 :   1.0 :     1 : False : False : Binary

        5 Constraint Declarations
            constraint_energy_customer : Size=1, Index=None, Active=False
                Key  : Lower : Body   : Upper                        : Active
                None :   0.0 : xa[C1] : xa[C71] - 24.839484696748443 :  False
            constraint_node_time_window : Size=1, Index=None, Active=False
                Key  : Lower : Body    : Upper : Active
                None :   0.0 : xw[C71] : 180.0 :  False
            constraint_payload : Size=1, Index=None, Active=False
                Key  : Lower : Body   : Upper        : Active
                None :   0.0 : xq[C1] : xq[C71] - 15 :  False
            constraint_time_customer : Size=1, Inde

In [100]:
m.instance.pprint()

16 Set Declarations
    ArcOff_index : Size=1, Index=None, Ordered=True
        Key  : Dimen : Domain  : Size : Members
        None :     2 : V0_*V1_ :  441 : {('D0', 'D1'), ('D0', 'S0'), ('D0', 'S3'), ('D0', 'S7'), ('D0', 'S13'), ('D0', 'S15'), ('D0', 'C61'), ('D0', 'C30'), ('D0', 'C98'), ('D0', 'C59'), ('D0', 'C35'), ('D0', 'C13'), ('D0', 'C10'), ('D0', 'C44'), ('D0', 'C50'), ('D0', 'C95'), ('D0', 'C18'), ('D0', 'C33'), ('D0', 'C85'), ('D0', 'C19'), ('D0', 'C40'), ('S0', 'D1'), ('S0', 'S0'), ('S0', 'S3'), ('S0', 'S7'), ('S0', 'S13'), ('S0', 'S15'), ('S0', 'C61'), ('S0', 'C30'), ('S0', 'C98'), ('S0', 'C59'), ('S0', 'C35'), ('S0', 'C13'), ('S0', 'C10'), ('S0', 'C44'), ('S0', 'C50'), ('S0', 'C95'), ('S0', 'C18'), ('S0', 'C33'), ('S0', 'C85'), ('S0', 'C19'), ('S0', 'C40'), ('S3', 'D1'), ('S3', 'S0'), ('S3', 'S3'), ('S3', 'S7'), ('S3', 'S13'), ('S3', 'S15'), ('S3', 'C61'), ('S3', 'C30'), ('S3', 'C98'), ('S3', 'C59'), ('S3', 'C35'), ('S3', 'C13'), ('S3', 'C10'), ('S3', 'C44'), ('S3', 'C50

        Key  : Active : Sense    : Expression
        None :   True : minimize : 36.235341863986875*xgamma[S3,D1] + 38.07886552931954*xgamma[S7,D1] + 24.08318915758459*xgamma[S13,D1] + 24.020824298928627*xgamma[S15,D1] + 22.360679774997898*xgamma[C61,D1] + 20.615528128088304*xgamma[C30,D1] + 30.805843601498726*xgamma[C98,D1] + 35.05709628591621*xgamma[C59,D1] + 38.07886552931954*xgamma[C35,D1] + 30.805843601498726*xgamma[C13,D1] + 16.76305461424021*xgamma[C10,D1] + 21.540659228538015*xgamma[C44,D1] + 22.80350850198276*xgamma[C50,D1] + 37.20215047547655*xgamma[C95,D1] + 35.35533905932738*xgamma[C18,D1] + 33.52610922848042*xgamma[C33,D1] + 29.732137494637012*xgamma[C85,D1] + 39.05124837953327*xgamma[C19,D1] + 20.615528128088304*xgamma[C40,D1] + 36.235341863986875*xgamma[S3,S0] + 38.07886552931954*xgamma[S7,S0] + 24.08318915758459*xgamma[S13,S0] + 24.020824298928627*xgamma[S15,S0] + 22.360679774997898*xgamma[C61,S0] + 20.615528128088304*xgamma[C30,S0] + 30.805843601498726*xgamma[C98,S0] +

        Key : Lower : Body                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                    : Upper : Active
        C10 :   0.0 : xgamma[C10,D1] + xgamma[C10,S0] + xgamma[C10,S3] + xgamma[C10,S7] + xgamma[C10,S13] + xgamma[C10,S15] + xgamma[C10,C61] + xgamma[C10,C30] + xgamma[C10,C98] + xgamma[C10,C59] + xgamma[C10,C35] + xgamma[C10,C13] + xgamma[C10,C44]

                Key            : Lower : Body                                                         : Upper : Active
                ('C10', 'C13') :   1.0 : ArcOn[C10,C13].indicator_var + ArcOff[C10,C13].indicator_var :   1.0 :   True
                ('C10', 'C18') :   1.0 : ArcOn[C10,C18].indicator_var + ArcOff[C10,C18].indicator_var :   1.0 :   True
                ('C10', 'C19') :   1.0 : ArcOn[C10,C19].indicator_var + ArcOff[C10,C19].indicator_var :   1.0 :   True
                ('C10', 'C30') :   1.0 : ArcOn[C10,C30].indicator_var + ArcOff[C10,C30].indicator_var :   1.0 :   True
                ('C10', 'C33') :   1.0 : ArcOn[C10,C33].indicator_var + ArcOff[C10,C33].indicator_var :   1.0 :   True
                ('C10', 'C35') :   1.0 : ArcOn[C10,C35].indicator_var + ArcOff[C10,C35].indicator_var :   1.0 :   True
                ('C10', 'C40') :   1.0 : ArcOn[C10,C40].indicator_var + ArcOff[C10,C40].indicator_var :   1.0 :   True
                ('C10', 'C44') :   1.0 : ArcOn[C

                            1 SetOf Declarations
                                ArcOn[C10,C85].indicator_var_index : Dimen=1, Size=1, Bounds=(None, None)
                                    Key  : Ordered : Members
                                    None :   False : UnindexedComponent_set

                            2 Declarations: ArcOn[C10,C85].indicator_var_index ArcOn[C10,C85].indicator_var

                    6 Declarations: localVarReferences ArcOn[C10,C85].constraint_xgamma ArcOn[C10,C85].constraint_node_time_window ArcOn[C10,C85].constraint_payload ArcOn[C10,C85].constraint_time_customer ArcOn[C10,C85].constraint_energy_customer
                _pyomo_gdp_bigm_reformulation.relaxedDisjuncts[23] : Active=True
                    2 Constraint Declarations
                        ArcOff[C10,C85].constraint_node_time_window : Size=2, Index=_pyomo_gdp_bigm_reformulation.lbub, Active=True
                            Key : Lower : Body                                              

...

            1 Var Declarations
                indicator_var : Size=1, Index=None
                    Key  : Lower : Value : Upper : Fixed : Stale : Domain
                    None :     0 :  -0.0 :     1 : False : False : Binary

            5 Constraint Declarations
                constraint_energy_customer : Size=1, Index=None, Active=False
                    Key  : Lower : Body    : Upper                        : Active
                    None :   0.0 : xa[S13] : xa[C85] - 52.839379254491625 :  False
                constraint_node_time_window : Size=1, Index=None, Active=False
                    Key  : Lower : Body    : Upper  : Active
                    None :   0.0 : xw[C85] : 1116.0 :  False
                constraint_payload : Size=1, Index=None, Active=False
                    Key  : Lower : Body    : Upper        : Active
                    None :   0.0 : xq[S13] : xq[C85] - 30 :  False
                constraint_time_customer : Size=1, Index=None, Active=False
      


            6 Declarations: indicator_var constraint_xgamma constraint_node_time_window constraint_payload constraint_time_customer constraint_energy_customer
        ArcOn[C98,S0] : Active=False
            1 Var Declarations
                indicator_var : Size=1, Index=None
                    Key  : Lower : Value : Upper : Fixed : Stale : Domain
                    None :     0 :  -0.0 :     1 : False : False : Binary

            5 Constraint Declarations
                constraint_energy_customer : Size=1, Index=None, Active=False
                    Key  : Lower : Body   : Upper                        : Active
                    None :   0.0 : xa[S0] : xa[C98] - 30.805843601498726 :  False
                constraint_node_time_window : Size=1, Index=None, Active=False
                    Key  : Lower : Body    : Upper  : Active
                    None :   0.0 : xw[C98] : 1115.0 :  False
                constraint_payload : Size=1, Index=None, Active=False
                    K

            5 Constraint Declarations
                constraint_energy_station : Size=1, Index=None, Active=False
                    Key  : Lower : Body    : Upper             : Active
                    None :   0.0 : xa[C98] : 46.94415639850128 :  False
                constraint_node_time_window : Size=1, Index=None, Active=False
                    Key  : Lower : Body   : Upper  : Active
                    None :   0.0 : xw[S0] : 1236.0 :  False
                constraint_payload : Size=1, Index=None, Active=False
                    Key  : Lower : Body    : Upper  : Active
                    None :   0.0 : xq[C98] : xq[S0] :  False
                constraint_time_station : Size=1, Index=None, Active=False
                    Key  : Lower : Body                                                : Upper   : Active
                    None :   0.0 : xw[S0] + 30.805843601498726 + 3.47*(77.75 - xa[S0]) : xw[C98] :  False
                constraint_xgamma : Size=1, Index=None, Active=

                    Key  : Lower : Body    : Upper             : Active
                    None :   0.0 : xa[C19] : 35.70240791674272 :  False
                constraint_node_time_window : Size=1, Index=None, Active=False
                    Key  : Lower : Body   : Upper  : Active
                    None :   0.0 : xw[S3] : 1236.0 :  False
                constraint_payload : Size=1, Index=None, Active=False
                    Key  : Lower : Body    : Upper  : Active
                    None :   0.0 : xq[C19] : xq[S3] :  False
                constraint_time_station : Size=1, Index=None, Active=False
                    Key  : Lower : Body                                               : Upper   : Active
                    None :   0.0 : xw[S3] + 42.04759208325728 + 3.47*(77.75 - xa[S3]) : xw[C19] :  False
                constraint_xgamma : Size=1, Index=None, Active=False
                    Key  : Lower : Body           : Upper : Active
                    None :   1.0 : xgamma[S3

        Key            : Disjuncts                             : Active : XOR
        ('C10', 'C13') : ['ArcOn[C10,C13]', 'ArcOff[C10,C13]'] :  False : True
        ('C10', 'C18') : ['ArcOn[C10,C18]', 'ArcOff[C10,C18]'] :  False : True
        ('C10', 'C19') : ['ArcOn[C10,C19]', 'ArcOff[C10,C19]'] :  False : True
        ('C10', 'C30') : ['ArcOn[C10,C30]', 'ArcOff[C10,C30]'] :  False : True
        ('C10', 'C33') : ['ArcOn[C10,C33]', 'ArcOff[C10,C33]'] :  False : True
        ('C10', 'C35') : ['ArcOn[C10,C35]', 'ArcOff[C10,C35]'] :  False : True
        ('C10', 'C40') : ['ArcOn[C10,C40]', 'ArcOff[C10,C40]'] :  False : True
        ('C10', 'C44') : ['ArcOn[C10,C44]', 'ArcOff[C10,C44]'] :  False : True
        ('C10', 'C50') : ['ArcOn[C10,C50]', 'ArcOff[C10,C50]'] :  False : True
        ('C10', 'C59') : ['ArcOn[C10,C59]', 'ArcOff[C10,C59]'] :  False : True
        ('C10', 'C61') : ['ArcOn[C10,C61]', 'ArcOff[C10,C61]'] :  False : True
        ('C10', 'C85') : ['ArcOn[C10,C85]', 'ArcOff[C